# <span style="color:#800000"> Cleaning the IkoKaziKE data</span>

<span style="color:orange">Here,I call in the data,check for missing values,keep what I need and use the BOW model </span>

In [190]:
#Import the necessary libraries
import re
import string 
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
from plotly import graph_objs as go
import nltk
import warnings
warnings.filterwarnings("ignore")
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem.porter import PorterStemmer
from nltk.stem import WordNetLemmatizer
from collections import Counter
from bs4 import BeautifulSoup

In [191]:
#import the dataset
df_tweet=pd.read_csv("twitter-job-hunter-chatbot.csv")
df_tweet.head()

Datetime                                               Text  \
0  18/07/2020 11:46  b"Ladies!!! #IkoKaziKE #IkoKazi Today, I reall...   
1  18/07/2020 11:18  b'#IkoKaziKe #IkoKazi Looking for a Audit Trai...   
2  18/07/2020 09:08  b'@moneychapKE are an online crowdfunding and ...   
3  18/07/2020 09:07  b'We are an online crowdfunding and fundraisin...   
4  18/07/2020 08:46  b'Striding into the weekend with a productive ...   

               Source                                          harsh tag  \
0      b'Mimimkenya7'                           ['IkoKaziKE', 'IkoKazi']   
1  b'MtandaoPromoter'                           ['IkoKaziKe', 'IkoKazi']   
2   b'KameneAndJalas'  ['KameneAndJalas', 'ikoJob', 'TwendeKaziKe', '...   
3      b'moneychapKE'                           ['IkoKazi', 'IkoKaziKE']   
4         b'amunsoft'  ['webdeveloper', 'business', 'IkoKazi', 'IkoKa...   

   Favourite Count  Retweets   6   7 submitter_name  
0              NaN     775.0 NaN NaN    Brian Cheye  
1              NaN       5.0 NaN NaN    Brian Cheye  
2              NaN   15675.0 NaN NaN    Brian Cheye  
3              NaN      79.0 NaN NaN    Brian Cheye  
4              NaN       2.0 NaN NaN    Brian Cheye

In [192]:
print(df_tweet.shape)

(29674, 9)


In [193]:
df_tweet.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 29674 entries, 0 to 29673
Data columns (total 9 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   Datetime         29674 non-null  object 
 1   Text             29674 non-null  object 
 2   Source           29460 non-null  object 
 3   harsh tag        4721 non-null   object 
 4   Favourite Count  29142 non-null  float64
 5   Retweets         27122 non-null  float64
 6   6                23075 non-null  float64
 7   7                23075 non-null  float64
 8   submitter_name   29674 non-null  object 
dtypes: float64(4), object(5)
memory usage: 2.0+ MB


In [194]:
#Variable Data types
df_tweet.dtypes

Datetime            object
Text                object
Source              object
harsh tag           object
Favourite Count    float64
Retweets           float64
6                  float64
7                  float64
submitter_name      object
dtype: object

# Cleaning the Data

In [195]:
df_tweet.isnull().sum()

Datetime               0
Text                   0
Source               214
harsh tag          24953
Favourite Count      532
Retweets            2552
6                   6599
7                   6599
submitter_name         0
dtype: int64

Since harsh tag has very many missing values that will be unreasonable to drop,
We fill the missing values with "no tag" the drop the rest of the na's

In [196]:
df_tweet["harsh tag"].fillna("no tag",inplace=True)

<span style="color:green">We can now drop the na values without worrying of dropping so many observations </span>

In [197]:
df_tweet.dropna(inplace=True)

In [198]:
#confirm in there are still na values
df_tweet.isnull().sum()

Datetime           0
Text               0
Source             0
harsh tag          0
Favourite Count    0
Retweets           0
6                  0
7                  0
submitter_name     0
dtype: int64

In [199]:
df_tweet.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 22865 entries, 4047 to 27121
Data columns (total 9 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   Datetime         22865 non-null  object 
 1   Text             22865 non-null  object 
 2   Source           22865 non-null  object 
 3   harsh tag        22865 non-null  object 
 4   Favourite Count  22865 non-null  float64
 5   Retweets         22865 non-null  float64
 6   6                22865 non-null  float64
 7   7                22865 non-null  float64
 8   submitter_name   22865 non-null  object 
dtypes: float64(4), object(5)
memory usage: 1.7+ MB


In [200]:
#check if we have any dulicates
print(df_tweet.duplicated().any())

True


In [201]:
#drop the duplicates
df_tweet.drop_duplicates(keep=False,inplace=True)

In [202]:
#Confirm if the duplicates have been dropped
print(df_tweet.duplicated().any())

False


In [203]:
df_tweet.describe()

Favourite Count      Retweets             6             7
count     2.280700e+04  22807.000000  2.280700e+04  22807.000000
mean      3.824571e+02      5.172535  3.560263e+02    147.239225
std       1.031095e+04     82.011641  1.030685e+04   1213.919912
min       0.000000e+00      0.000000  0.000000e+00      0.000000
25%       0.000000e+00      0.000000  0.000000e+00      0.000000
50%       1.000000e+00      0.000000  0.000000e+00      0.000000
75%       2.000000e+00      2.000000  0.000000e+00      0.000000
max       1.496504e+06   4167.000000  1.496395e+06  28407.000000

# <u><span style="color:orange"> Dealing with outliers </span></u>

In [204]:
from scipy import stats
num = ['Retweets']

for i, col in enumerate(num):
    z=np.abs(stats.zscore(df_tweet[col]))
print(z)

[0.06307212 0.06307212 0.05087846 ... 0.05087846 0.05087846 0.06307212]


In [205]:
#subset the data with observations whose z score is less than 3
df1=df_tweet[(z<3)]
print (f"Data frame with outliers had : {(df_tweet.shape[0])}")
print(f"Data frame without outliers has : {df1.shape[0]}")


Data frame with outliers had : 22807
Data frame without outliers has : 22768


In [206]:
#remove spaces and convert the variable names to lower
df1.columns=df1.columns.str.lower().str.strip()

In [207]:
#Cleaning text,lower remove punctuation,white space
#create a function then use it to clean the column texts
'''Make text lowercase, remove text in square brackets,remove links,remove punctuation
    and remove words containing numbers.'''
def clean_text(text):
    text=str(text).lower()
    text=re.sub('\[.*?\]','',text)   # question marks,square brackets
    text = re.sub('https?://\S+|www\.\S+', '', text)
    text = re.sub('<.*?>+', '', text)
    text = re.sub('[%s]' % re.escape(string.punctuation), '', text)
    text = re.sub('\n', '', text)
    text = re.sub('\w*\d\w*', '', text)
    return text           


In [208]:
df1['text']= df1['text'].apply(lambda x:clean_text(x))
df1['source']=df1['source'].apply(lambda x:clean_text(x))

In [209]:
df1.head()

datetime  \
4047  2020-07-18 10:16:18+00:00   
4048  2020-07-18 10:09:08+00:00   
4049  2020-07-18 10:05:52+00:00   
4050  2020-07-18 10:05:22+00:00   
4051  2020-07-18 10:05:16+00:00   

                                                   text        source  \
4047  job seekers  free cover letter template   ikok...   simoningari   
4048  get the latest and best car shade and all cust...    simonmagak   
4049  join jobalertke for latest updates on     ikok...   simoningari   
4050  hey people im looking for a farm manager with ...  vidolebaridi   
4051  job hunting can be emotionally draining  to en...   simoningari   

     harsh tag  favourite count  retweets       6       7  submitter_name  
4047    no tag              1.0       0.0  4342.0  4994.0  Dennis Mwaniki  
4048    no tag              0.0       0.0    28.0    92.0  Dennis Mwaniki  
4049    no tag              2.0       1.0  4342.0  4994.0  Dennis Mwaniki  
4050    no tag              0.0       0.0   141.0   485.0  Dennis Mwaniki  
4051    no tag              0.0       0.0  4342.0  4994.0  Dennis Mwaniki

In [210]:
#use a subset of what I need.
df_bow = df1[["datetime" ,"text","source","harsh tag","retweets"]]  #get rid of 6,7 and submitter_name

In [211]:
df_bow.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 22768 entries, 4047 to 27121
Data columns (total 5 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   datetime   22768 non-null  object 
 1   text       22768 non-null  object 
 2   source     22768 non-null  object 
 3   harsh tag  22768 non-null  object 
 4   retweets   22768 non-null  float64
dtypes: float64(1), object(4)
memory usage: 1.0+ MB


In [212]:
df_bow.dtypes

datetime      object
text          object
source        object
harsh tag     object
retweets     float64
dtype: object

# <span style="color:maroon">Bag of words Model </span>

Procedure 
<br> 1.Tokenize </br>
<br> 2.Remove Stopwords</br>
<br> 3.Stemming/Lematization</br>
<br> 4.Modelling with BOW
<br> 0. Split Test and Train Data <br>

In [213]:
#1.Tokenizing
nltk.download('punkt')
nltk.download('wordnet')


[nltk_data] Downloading package punkt to C:\Users\Eunice
[nltk_data]     Mutahi\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to C:\Users\Eunice
[nltk_data]     Mutahi\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [214]:
df_bow['text_list'] = df_bow['text'].apply(lambda x:str(x).split())   #Use tokenize or split..same results
top = Counter([item for sublist in df_bow['text_list'] for item in sublist])  #counts the frequency of words
temp = pd.DataFrame(top.most_common(5))  #A dataframe of top 5
temp.columns = ['Common_words','count']
temp.style.background_gradient(cmap='Blues')

In [215]:
df_bow.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 22768 entries, 4047 to 27121
Data columns (total 6 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   datetime   22768 non-null  object 
 1   text       22768 non-null  object 
 2   source     22768 non-null  object 
 3   harsh tag  22768 non-null  object 
 4   retweets   22768 non-null  float64
 5   text_list  22768 non-null  object 
dtypes: float64(1), object(5)
memory usage: 1.2+ MB


In [216]:
df_bow['text_list'][0:20]

4047    [job, seekers, free, cover, letter, template, ...
4048    [get, the, latest, and, best, car, shade, and,...
4049    [join, jobalertke, for, latest, updates, on, i...
4050    [hey, people, im, looking, for, a, farm, manag...
4051    [job, hunting, can, be, emotionally, draining,...
4052         [job, whatsapp, groups, to, join, ikokazike]
4053    [i, am, looking, for, good, carpenter, to, do,...
4054    [kot, were, still, taking, applications, for, ...
4055    [the, east, african, community, is, looking, f...
4056    [vacancy, at, miritini, medical, labtech, qual...
4057    [quality, handbags, available, in, all, colors...
4058                                          [ikokazike]
4059    [moneychapke, are, an, online, crowdfunding, a...
4060    [we, are, an, online, crowdfunding, and, fundr...
4061           [let’s, make, your, life, easy, ikokazike]
4062    [striding, into, the, weekend, with, a, produc...
4063    [years, content, community, mgt, at, a, fast, ...
4064    [whats

In [217]:
# 2. Removing Stop words
#def remove_stopwords(x):
    #return [y for y in x if y not in set(stopwords.words('english'))]
#df_bow['text_list']=df_bow['text_list'].apply(lambda x: remove_stopwords(x))    
    

In [218]:
len(df_bow['text_list'])

22768

# Lemmatization Vs Stemming  (<span style="color:blue">What you need to know!!!</span>)

Stemming produces an intermediate representation of a word that is not meaningfull e.g friendli.
Lemmatization on the other hand gets the root word thats meaningful though it takes longer to do this.

Stemming can be used in Sentiment analysis and Lemmatization can be applied in chatbots since you need the answers to be meaningful

# Stemming  
<span style="color:blue"> In the following cell, we prepare our text for stemming by removing any html parsers,tokenizing and removing the stopwords. We shall then use the Porter Stemmer to stem our words.

In [219]:
def prep_text(text) :
    import nltk
   
     # 1. Remove HTML.
    my_text = BeautifulSoup(text,"html.parser").get_text()
    
    #Tokenize words
    tokens=nltk.word_tokenize(my_text)
    
    #Define stopwords
    stops=set(stopwords.words("english"))
    # Convert the stopwords list to "set" data type.
    #stops = set(nltk.corpus.stopwords.words("english"))
    
    #Remove the stopwords
    words=[x for x in tokens if  not x in stops]
    #print(words)
    
    #stemming
    stemmer=PorterStemmer()
    stemmed_words = []
    for i in range(0,len(words)):
        l2=' '.join([stemmer.stem(word) for word in words])
        stemmed_words.append(l2)
    #words=[nltk.stem.SnowballStemmer('english').stem(w) for w in words] 
    
    #join the words back into one string sepereated by space and return results
    return stemmed_words

In [220]:
#Performing the iterative preps on each of the statements
df_bow['text_stem']=df_bow['text'].apply(prep_text)

In [221]:
stemmer=PorterStemmer()
stemmer.stem("hiring")

'hire'

In [222]:
#View the Stemmed words
df_bow.sample(5)

datetime  \
15633  2020-07-17 10:13:45+00:00   
8510   2020-07-17 11:30:57+00:00   
25250  2020-06-29 07:56:06+00:00   
8734   2020-07-16 15:13:45+00:00   
7479   2020-07-01 09:52:13+00:00   

                                                    text        source  \
15633          ikokazike sweaters available whatsap me                   
8510   nz gov mbie is hiring a personal assistantteam...    joblifyapp   
25250  welcome to realtimestudioske  were here to ser...    realtimeke   
8734    rpf upcoming vacancy out kijiye sir aur na la...                 
7479   hilton home products offers beautiful and crea...  hiltonhomeke   

      harsh tag  retweets                                          text_list  \
15633    no tag       4.0      [ikokazike, sweaters, available, whatsap, me]   
8510     no tag       0.0  [nz, gov, mbie, is, hiring, a, personal, assis...   
25250    no tag       3.0  [welcome, to, realtimestudioske, were, here, t...   
8734     no tag       4.0  [rpf, upcoming, vacancy, out, kijiye, sir, aur...   
7479     no tag       0.0  [hilton, home, products, offers, beautiful, an...   

                                               text_stem  
15633  [ikokazik sweater avail whatsap, ikokazik swea...  
8510   [nz gov mbie hire person assistantteam adminis...  
25250  [welcom realtimestudiosk serv reach us qualiti...  
8734   [rpf upcom vacanc kijiy sir aur na late kijiy ...  
7479   [hilton home product offer beauti creativ gyps...

In [110]:
# 3.1 Stemming
#stemmer=PorterStemmer()
#text_stem=[]
#for i in range(len(df_bow['text'])):
    #for i in range(len(df_bow['text_list'])):
    #my_text=nltk.word_tokenize(df_bow['text'])
    #my_text=df_bow['text'].apply(lambda x:str(x).split())
    #print(my_text)
    #my_text=[stemmer.stem(word) for word in my_text if word not in set(stopwords.words("english"))]
   # my_text=' '.join(my_text)
    #text_stem.append(my_text)


# Lemmatization 
<span style="color:red"> In the following cell, we prepare our text for lemmatization by removing any html parsers,tokenizing and removing the stopwords. We shall then use the WordNet Lemmatizer to lemmatize our words.


In [223]:
# preping text for BOW :remove stopwords and lemmatize

def prep_lem(text) :
    import nltk
   
     # 1. Remove HTML.
    my_text = BeautifulSoup(text,"html.parser").get_text()
    
    #Tokenize words
    tokens=nltk.word_tokenize(my_text)
    
    #Define stopwords
    stops=set(stopwords.words("english"))
    # Convert the stopwords list to "set" data type.
    #stops = set(nltk.corpus.stopwords.words("english"))
    
    #Remove the stopwords
    #words=[x for x in tokens if  not x in stops]
    words=[x for x in tokens if  not x in stops]
    
    #Creating the bag of words model
    wordscount={}
    
    for data in my_text:
        for word in words:
            if word not in wordscount.keys():
                wordscount[word]= 1
            else:
                wordscount[word] += 1
    print(wordscount)
    
    #lematizing
    lemmatizer=WordNetLemmatizer()
    lemmatized_words=[]
    
    for i in range(0,len(words)):
        lemma=' '.join([lemmatizer.lemmatize(word, pos="v") for word in words])
        lemmatized_words.append(lemma)
    
    #for word in words:
         #print ("{0:10}{1:10}".format(word,lemmatizer.lemmatize(word, pos="v")))
            #words=[lemmatizer.lemmatize(word, pos="v")]
        #words=[lemmatizer.lemmatize(word,pos="a") for word in words]
   # print(" ".join(words))
    
    #join the words back into one string sepereated by space and return results
  
    
    
    return lemmatized_words

        

In [224]:
#Performing the iterative preps on each of the statements
df_bow['text_lem']=df_bow['text'].apply(prep_lem)

{'job': 81, 'seekers': 81, 'free': 81, 'cover': 81, 'letter': 81, 'template': 81, 'ikokazike': 81, 'patakazike': 81, 'gethired': 81, 'jobseeker': 81}
{'get': 178, 'latest': 178, 'best': 178, 'car': 178, 'shade': 178, 'customised': 178, 'canopies': 178, 'pollycarbonate': 178, 'shades': 178, 'cabro': 178, 'affordable': 178, 'prices': 178, 'call': 178, 'us': 178, 'president': 178, 'kenyatta': 178, 'atwoli': 178, 'mpesa': 178, 'ikokazike': 178, 'babuowino': 178}
{'join': 173, 'jobalertke': 173, 'latest': 173, 'updates': 173, 'ikokazike': 173, 'patakazike': 173, 'gethired': 173, 'jobseekers': 173, 'jobs': 173, 'internships': 173, 'recruitment': 173, 'talent': 173, 'recruiters': 173, 'interns': 173, 'scholarships': 173, 'job': 173, 'jobalert': 173, 'hr': 173, 'hiring': 173}
{'hey': 165, 'people': 165, 'im': 165, 'looking': 165, 'farm': 165, 'manager': 165, 'specialisation': 165, 'animal': 165, 'husbandry': 165, 'addition': 165, 'experience': 165, 'agriculture': 165, 'addvantage': 165, 'ikoka

{'looking': 151, 'job': 302, 'opportunities': 151, 'check': 151, 'workshop': 151, 'manager': 151, '–': 151, 'dar': 151, 'es': 151, 'salaam': 151, 'tanzania': 151, 'click': 151, 'apply': 151, 'ikokazike': 151, 'ikokazi': 151, 'hiring': 151, 'jobopening': 151}
{'looking': 148, 'job': 296, 'opportunities': 148, 'check': 148, 'freelance': 148, 'staff': 148, 'researchers': 148, 'writers': 148, 'click': 148, 'apply': 148, 'ikokazike': 148, 'ikokazi': 148, 'hiring': 148, 'jobopening': 148}
{'looking': 130, 'job': 260, 'opportunities': 130, 'check': 130, 'warehouse': 130, 'supervisor': 130, 'click': 130, 'apply': 130, 'ikokazike': 130, 'ikokazi': 130, 'hiring': 130, 'jobopening': 130}
{'looking': 131, 'job': 262, 'opportunities': 131, 'check': 131, 'sales': 131, 'executive': 131, 'nyeri': 131, 'click': 131, 'apply': 131, 'ikokazike': 131, 'ikokazi': 131, 'hiring': 131, 'jobopening': 131}
{'looking': 145, 'job': 290, 'opportunities': 145, 'check': 145, 'digital': 145, 'media': 145, 'customer': 

{'worldemojiday': 91, 'describe': 91, 'using': 91, 'emoji': 91, 'hiring': 91, 'ikokazike': 91, 'jobs': 91, 'fridayfeeling': 91}
{'ikokazike': 12, '¿': 12}
{'youre': 98, 'kitengala': 98, 'looking': 98, 'opportunity': 98, 'kindly': 98, 'reach': 98, 'us': 98, 'via': 98, 'whatsapp': 196, 'ikokazike': 98}
{'im': 213, 'nduati': 213, 'wambugu': 213, 'talented': 213, 'business': 213, 'analyst': 213, 'software': 213, 'engineer': 213, 'years': 213, 'experience': 213, 'looking': 213, 'consultancyfull': 213, 'time': 213, 'job': 213, 'kindly': 213, 'rt': 213, 'employer': 213, 'might': 213, 'tl': 213, 'nwambuguegmailcom': 213, 'ikokazike': 213}
{'communications': 57, 'officer': 57, 'refugepoint': 57, 'salary': 57, 'kes': 57, 'ikokazike': 57}
{'python': 246, 'ikokazike': 246, 'candidate': 246, 'required': 492, 'minimum': 246, 'max': 246, 'years': 246, 'experience': 246, 'dynamics': 246, 'indepth': 246, 'dev': 246, 'technical': 246, 'skills': 246, 'fo': 246, 'power': 246, 'bi': 246, 'ssrs': 246, 'x': 

{'every': 228, 'journey': 228, 'needs': 228, 'passport': 456, 'stylish': 228, 'external': 228, 'hard': 228, 'disk': 228, 'compatible': 228, 'mac': 228, 'book': 228, 'laptop': 228, 'tablet': 228, 'entertainment': 228, 'system': 228, 'need': 228, 'help': 228, 'ordering': 228, 'call': 228, 'whatsapp': 228, 'emojiday': 228, 'ikokazike': 228, 'sportpesa': 228}
{'overwhelmed': 242, 'financial': 242, 'administrative': 242, 'burden': 484, 'associated': 242, 'hiring': 242, 'contract': 242, 'labor': 242, 'ease': 242, 'visit': 242, 'today': 242, 'find': 242, 'exactly': 242, 'sheerlogicmanagement': 242, 'humanresource': 242, 'ikokazike': 242}
{'new': 108, 'post': 108, 'internship': 108, 'opportunities': 108, 'african': 108, 'institute': 108, 'development': 108, 'ikokazi': 108, 'ikokazike': 108, 'financeinternships': 108}
{'post': 72, 'edited': 72, 'career': 72, 'opportunities': 72, 'aga': 72, 'khan': 72, 'hospital': 72, 'ikokazi': 72, 'ikokazike': 72}
{'new': 69, 'post': 69, 'career': 69, 'opportu

{'master': 99, 'virtual': 99, 'job': 99, 'hunt': 99, 'tips': 99, 'getting': 99, 'hired': 99, 'home': 99, 'ikokazike': 99, 'jobsinkenya': 99, 'ikokazi': 99, 'jobske': 99}
{'hello': 269, 'know': 269, 'anybody': 269, 'looking': 538, 'printing': 269, 'amp': 538, 'general': 269, 'branding': 269, 'services': 269, 'every': 269, 'anything': 269, 'affordable': 269, 'rate': 269, 'please': 269, 'feel': 269, 'free': 269, 'hit': 269, 'dm': 269, 'kindly': 269, 'retweet': 269, 'customers': 269, 'could': 269, 'timeline': 269, 'thank': 269, 'ikokazike': 269}
{'ikokazike': 25, 'tips': 25, 'women': 25}
{'mary': 78, 'robinson': 78, 'climate': 78, 'justice': 78, 'award': 78, 'fully': 78, 'funded': 78, 'ikokazike': 78, 'patakazike': 78, 'gethi': 78}
{'one': 79, 'world': 79, 'media': 79, 'coronavirus': 79, 'reporting': 79, 'award': 79, 'ikokazike': 79, 'patakazike': 79, 'gethired': 79, 'jo': 79}
{'insead': 79, 'mba': 79, 'nelson': 79, 'mandela': 79, 'endowed': 79, 'scholarship': 79, 'ikokazike': 79, 'patakaz

...

{'ikokazike': 67, 'follow': 67, 'telegram': 67, 'channel': 67, 'instant': 67, 'job': 67, 'notifications': 67}
{'need': 104, 'help': 104, 'land': 104, 'dream': 104, 'job': 104, 'reach': 104, 'career': 104, 'coach': 104, 'assist': 104, 'send': 104, 'dm': 104, 'jobsearch…': 104}
{'sell': 106, 'wallpapers': 106, 'inclusive': 106, 'installation': 106, 'theres': 106, 'wide': 106, 'range': 106, 'selection': 106, 'ayumathe': 106, 'call': 106, 'whatsapp': 106, '…': 106}
{'hi': 114, 'twitter': 114, 'ikokazikelooking': 114, 'someone': 114, 'supply': 114, 'flower': 114, 'boxes': 228, 'gift': 114, 'different': 114, 'shapes…': 114}
{'theres': 101, 'wide': 101, 'range': 101, 'wallpapers': 101, 'inclusive': 101, 'installation': 101, 'store': 101, 'dm': 101, 'call': 101, 'whatsapp': 101, '…': 101}
{'qualified': 73, 'interns': 73, 'posted': 73, 'job': 73, 'might': 73, 'interested': 73}
{'hiringwe': 113, 'looking': 113, 'volunteer': 113, 'interns': 113, 'content': 113, 'creation': 113, 'social': 113, 'me

{'ikokazike': 77, 'join': 77, 'telegram': 77, 'channel': 77, 'jobsearchke': 77, 'instant': 77, 'job': 77, 'notifications': 77}
{'wireless': 90, 'keyboard': 90, 'communicates': 90, 'using': 90, 'signals': 90, 'range': 90, 'mhz': 90, 'ghz': 90, 'call': 90, '…': 90}
{'ikokazike': 64, 'sales': 64, 'executives': 64, 'sheer': 64, 'logic': 64, 'massive': 64, 'recruitement': 64}
{'ikokazike': 54, 'procurement': 54, 'officer': 54, 'job': 54, 'transport': 54, 'industry': 54}
{'charitymuchiri': 55, 'ikokazike': 55, 'saccharineshrty': 55, 'thank': 55, 'swee': 55}
{'ikokazike': 75, 'saccharineshrty': 75, 'ecessie': 75, 'graphic': 75, 'designer': 75, 'friend': 75, 'see': 75}
{'professional': 116, 'paint': 232, 'experts': 116, 'ready': 116, 'help': 116, 'put': 116, 'finishing': 116, 'touches': 116, 'home': 116, 'renovation': 116, 'or…': 116}
{'new': 51, 'post': 51, 'job': 51, 'opening': 51, 'silensec': 51, 'ikokazi': 51, 'ikokazike': 51}
{'ikokazike': 51, 'hustle': 51, 'essievibes': 51, 'share': 51, 

{'call': 82, 'ajira': 82, 'mentors': 82, 'ikokazike': 82, 'patakazike': 82, 'gethired': 82, 'jobseekers': 82, 'jobs': 82, 'internship': 82}
{'qualified': 91, 'sales': 91, 'position': 91, 'simoningari': 91, 'posted': 91, 'job': 91, 'might': 91, 'interested': 91}
{'good': 115, 'afternoon': 115, 'ladies': 115, 'gentlemen': 115, 'size': 115, '👇support': 115, 'sis': 115, 'retweeting': 115, 'making': 115, 'order': 115, 'inquiry': 115, '❤❤…': 115}
{'kot': 112, 'anyone': 112, 'good': 112, 'job': 112, 'want': 112, 'excellent': 112, 'spin': 112, 'reach': 112, 'mungeizm': 112, 'matters': 112, 'design': 112, 'an…': 112}
{'youre': 109, 'job': 109, 'interview': 109, 'tell': 109, 'entanglement': 109, 'relationship': 109, 'ikokazike': 109, 'hiring…': 109}
{'unataka': 76, 'kusema': 76, 'pal': 76, 'alianzisha': 76, 'ikokazike': 76, 'look': 76, 'greener': 76, 'pastures': 76, '😭😭😭': 76}
{'kama': 113, 'unatoka': 113, 'north': 113, 'rift': 113, 'ama': 113, 'western': 113, 'kenya': 113, 'especially': 113, 'e

{'ikokazike': 28, 'consultant': 28, 'needed': 28}
{'looking': 86, 'icpak': 86, 'registered': 86, 'accountant': 86, 'small': 86, 'time': 86, 'job': 86, 'like': 86, 'daysikokazike': 86}
{'create': 112, 'design': 112, 'right': 112, 'message': 112, 'audience': 112, 'outstanding': 112, 'companyprofileget': 112, 'touch…': 112}
{'financial': 94, 'consultant': 94, 'yes': 94, 'pioneer': 94, 'assurance': 94, 'looking': 94, 'skills': 94, 'apply': 94, 'now…': 94}
{'normal': 107, 'cabros': 107, 'available': 107, 'square': 107, 'metre': 107, 'buying': 107, 'price': 107, 'including': 107, 'delivery': 107, 'installationfixing': 107, 'wi…': 107}
{'numberikokazike': 25, '😎': 25}
{'im': 109, 'creative': 109, 'mind': 109, 'major': 109, 'fine': 109, 'arts': 109, 'interior': 109, 'design': 218, 'product': 109, 'branding': 109, 'team': 109, 'building': 109, 'are…': 109}
{'industrial': 85, 'attachment': 85, 'opportunity': 85, 'kenya': 85, 'wildlife': 85, 'trust': 85, 'ikokazike': 85, 'patakazike': 85, 'get': 

{'looking': 89, 'job': 89, 'opportunities': 89, 'check': 89, 'project': 89, 'manager': 89, 'jobclick': 89, 'apply': 89}
{'looking': 114, 'job': 114, 'opportunities': 114, 'check': 114, 'national': 114, 'technical': 114, 'expert': 114, 'deputy': 114, 'team': 114, 'leader': 114, 'snv': 114, 'netherlands…': 114}
{'looking': 113, 'job': 113, 'opportunities': 113, 'check': 113, 'legal': 113, 'office': 113, 'east': 113, 'african': 113, 'community': 113, 'eac': 113, 'jobclick': 113, 'ap…': 113}
{'looking': 99, 'job': 99, 'opportunities': 99, 'check': 99, 'research': 99, 'scientist': 99, 'ibm': 99, 'jobclick': 99, 'apply…': 99}
{'looking': 114, 'job': 114, 'opportunities': 114, 'check': 114, 'information': 114, 'technology': 114, 'officer': 114, 'east': 114, 'african': 114, 'community': 114, 'eac': 114, 'jo…': 114}
{'looking': 108, 'job': 108, 'opportunities': 108, 'check': 108, 'project': 108, 'coordinator': 108, 'farm': 108, 'africa': 108, 'jobclick': 108, 'apply…': 108}
{'looking': 109, 'jo

In [225]:
lemmatizer=WordNetLemmatizer()
word=lemmatizer.lemmatize("looking",pos="v")
print(word)

look


In [226]:
#view a sample
df_bow.sample(10)

datetime  \
14659  2020-06-17 16:28:54+00:00   
17283  2020-07-09 17:02:14+00:00   
23220  2020-07-09 17:36:32+00:00   
24320  2020-07-04 06:10:06+00:00   
18718  2020-07-01 22:05:45+00:00   
11771  2020-07-03 09:29:17+00:00   
7619   2020-06-30 13:43:05+00:00   
21565  2020-07-18 07:05:34+00:00   
20453  2020-07-18 15:00:47+00:00   
20314  2020-07-18 15:50:29+00:00   

                                                    text           source  \
14659   production supervisor at himatrade limited – ...      hotproforum   
17283  looking for more job opportunities check out t...        kaziquest   
23220         ikokazike ikokazi employment opportunities      robbytwayne   
24320  job opening ikokazike kenya institute of curri...    findjobskenya   
18718  looking for more job opportunities check out t...        kaziquest   
11771   bricklaying apprentice yarlington housing gro...  skillupsomerset   
7619   the big five breweries hiring waiterswaitresse...      simoningari   
21565  postulez dès maintenant pour manpowerfrance en...   melaniecaurier   
20453  check out project accounting analyst in dallas...   archdrecruiter   
20314  mahindra finance board approves rights issue p...       iamnetwork   

      harsh tag  retweets                                          text_list  \
14659    no tag       0.0  [production, supervisor, at, himatrade, limite...   
17283    no tag      11.0  [looking, for, more, job, opportunities, check...   
23220    no tag       0.0    [ikokazike, ikokazi, employment, opportunities]   
24320    no tag       0.0  [job, opening, ikokazike, kenya, institute, of...   
18718    no tag       1.0  [looking, for, more, job, opportunities, check...   
11771    no tag       5.0  [bricklaying, apprentice, yarlington, housing,...   
7619     no tag       0.0  [the, big, five, breweries, hiring, waiterswai...   
21565    no tag       0.0  [postulez, dès, maintenant, pour, manpowerfran...   
20453    no tag       0.0  [check, out, project, accounting, analyst, in,...   
20314    no tag       1.0  [mahindra, finance, board, approves, rights, i...   

                                               text_stem  \
14659  [product supervisor himatrad limit – hotprooru...   
17283  [look job opportun check senior full stack eng...   
23220  [ikokazik ikokazi employ opportun, ikokazik ik...   
24320  [job open ikokazik kenya institut curriculum d...   
18718  [look job opportun check ceo manag job click a...   
11771  [bricklay apprentic yarlington hous group appr...   
7619   [big five breweri hire waiterswaitress ikokazi...   
21565  [postulez dè mainten pour manpowerfr en tant q...   
20453  [check project account analyst dallastx job, c...   
20314  [mahindra financ board approv right issu plan ...   

                                                text_lem  
14659  [production supervisor himatrade limit – hotpr...  
17283  [look job opportunities check senior full stac...  
23220  [ikokazike ikokazi employment opportunities, i...  
24320  [job open ikokazike kenya institute curriculum...  
18718  [look job opportunities check ceo manager job ...  
11771  [bricklaying apprentice yarlington house group...  
7619   [big five breweries hire waiterswaitresses iko...  
21565  [postulez dès maintenant pour manpowerfrance e...  
20453  [check project account analyst dallastx job, c...  
20314  [mahindra finance board approve right issue pl...

The following is a good example to see how tokenizing, stemming and removal of stopwords actually works

In [228]:
#Lets look at the top 20 most common words after removing stopwords and lemmatizing
df_bow['text_lem'] = df_bow['text_lem'].apply(lambda x:str(x).split())
top = Counter([item for sublist in df_bow['text_lem'] for item in sublist])
temp = pd.DataFrame(top.most_common(20))
temp.columns = ['Common_words','count']
temp.style.background_gradient(cmap='Blues')

In [230]:
df_bow.sample(10)

datetime  \
5120   2020-07-14 07:18:55+00:00   
6075   2020-07-09 05:42:09+00:00   
16928  2020-07-10 22:56:58+00:00   
19203  2020-06-29 13:52:14+00:00   
17012  2020-07-10 15:32:42+00:00   
20365  2020-07-18 15:27:53+00:00   
19629  2020-07-18 21:29:53+00:00   
18842  2020-07-01 09:20:12+00:00   
9497   2020-07-14 13:32:25+00:00   
16777  2020-07-12 13:57:44+00:00   

                                                    text           source  \
5120   ikokazike hr assistant at united nations devel...      jobsearchke   
6075   conservative employers have little or no room ...       businesske   
16928  consultancy for the analysis of outofschool da...      datanomadke   
19203                                         ikokazike       mercymurugi   
17012  are you a financial consultant if yes pioneer ...     emploiafrica   
20365  localworkca is looking for an inhome usage tes...      localworkca   
19629  new job opening at junologistics in itascail c...    junologistics   
18842   theres no shortage of innovation theres just ...          mandere   
9497   vacancy front desk officers needed for recruit...  consultantpandj   
16777  ikokazike i am looking for a react native deve...            aboue   

      harsh tag  retweets                                          text_list  \
5120     no tag       0.0  [ikokazike, hr, assistant, at, united, nations...   
6075     no tag       1.0  [conservative, employers, have, little, or, no...   
16928    no tag       3.0  [consultancy, for, the, analysis, of, outofsch...   
19203    no tag       3.0                                        [ikokazike]   
17012    no tag       1.0  [are, you, a, financial, consultant, if, yes, ...   
20365    no tag       0.0  [localworkca, is, looking, for, an, inhome, us...   
19629    no tag       0.0  [new, job, opening, at, junologistics, in, ita...   
18842    no tag       0.0  [theres, no, shortage, of, innovation, theres,...   
9497     no tag       0.0  [vacancy, front, desk, officers, needed, for, ...   
16777    no tag       2.0  [ikokazike, i, am, looking, for, a, react, nat...   

                                               text_stem  \
5120   [ikokazik hr assist unit nation develop progra...   
6075   [conserv employ littl room job hopper ikokazik...   
16928  [consult analysi outofschool data cameroon ken...   
19203                                         [ikokazik]   
17012  [financi consult ye pioneer assur look skill a...   
20365  [localworkca look inhom usag tester product te...   
19629  [new job open junologist itascail custom compl...   
18842  [there shortag innov there shortag use innov m...   
9497   [vacanc front desk offic need recruit need des...   
16777  [ikokazik look react nativ develop, ikokazik l...   

                                                text_lem  
5120   [['ikokazike, hr, assistant, unite, nations, d...  
6075   [['conservative, employers, little, room, job,...  
16928  [['consultancy, analysis, outofschool, data, c...  
19203                                    [['ikokazike']]  
17012  [['financial, consultant, yes, pioneer, assura...  
20365  [['localworkca, look, inhome, usage, tester, p...  
19629  [['new, job, open, junologistics, itascail, cu...  
18842  [['theres, shortage, innovation, theres, short...  
9497   [['vacancy, front, desk, officer, need, recrui...  
16777  [['ikokazike, look, react, native, developer',...

# Bag of words

# Lets obtain the most frequent words in our text

<br>Here we declare a dictionary that will hold our bag of words</br>
<br>For each word in each sentence, we check if it exists in our dictionary</br>
<br>If the word already exists,we increement its count with 1 (+1),if it doesnt exist,we add it to our dictionary with a count of 1</br>

In [250]:
#Creating the bag of words model
#wordscount={}

#words=nltk.word_tokenize(df_bow['text'])

#for word in words:
    #if word not in wordscount.keys():
        #wordscount[word]= 1
    #else:
        #wordscount[word] += 1

In [130]:
from sklearn.feature_extraction.text import CountVectorizer
cv=CountVectorizer()

In [247]:
corpus =df_bow['text']
#doc_set=df_bow['text_lem']
cv=CountVectorizer(stop_words='english', analyzer='word') #ngram_range=(2, 3) you can specify the groupings using ngram

bow=cv.fit_transform(corpus)

#View the vocabulary and frequency
cv.vocabulary_

{'job': 10815,
 'seekers': 18952,
 'free': 7758,
 'cover': 4559,
 'letter': 12297,
 'template': 21080,
 'ikokazike': 9787,
 'patakazike': 15836,
 'gethired': 8199,
 'jobseeker': 10954,
 'latest': 12098,
 'best': 2109,
 'car': 3094,
 'shade': 19170,
 'customised': 4838,
 'canopies': 3064,
 'pollycarbonate': 16474,
 'shades': 19171,
 'cabro': 2932,
 'affordable': 428,
 'prices': 16770,
 'president': 16742,
 'kenyatta': 11511,
 'atwoli': 1476,
 'mpesa': 14080,
 'babuowino': 1662,
 'join': 11103,
 'jobalertke': 10825,
 'updates': 22259,
 'jobseekers': 10955,
 'jobs': 10926,
 'internships': 10334,
 'recruitment': 17577,
 'talent': 20765,
 'recruiters': 17568,
 'interns': 10328,
 'scholarships': 18772,
 'jobalert': 10824,
 'hr': 9435,
 'hiring': 9196,
 'hey': 9097,
 'people': 16011,
 'im': 9836,
 'looking': 12669,
 'farm': 7150,
 'manager': 13041,
 'specialisation': 19865,
 'animal': 942,
 'husbandry': 9579,
 'addition': 270,
 'experience': 6950,
 'agriculture': 514,
 'addvantage': 278,
 'rt

In [239]:
#Get the feature names (variable names)
cv.get_feature_names()


['aa',
 'aaafm',
 'aadhar',
 'aads',
 'aaiwa',
 'aaj',
 'aajkijandhara',
 'aajtak',
 'aalasijobrolengcom',
 'aampm',
 'aan',
 'aane',
 'aangename',
 'aantal',
 'aap',
 'aar',
 'aarzel',
 'aas',
 'aat',
 'aatfafrica',
 'aatmanirbharbharat',
 'aatmanirbharbharatabhiyan',
 'aatmnirbharbharat',
 'aavs',
 'aayega',
 'aayegi',
 'aaz',
 'ab',
 'aba',
 'ababa',
 'abandon',
 'abap',
 'abated',
 'abb',
 'abbandonoto',
 'abbey',
 'abbieholidays',
 'abc',
 'abcbankcareers',
 'abcsharktank',
 'abd',
 'abdncyrenians',
 'abdul',
 'abenton',
 'abentra',
 'aber',
 'abercynonglamorgan',
 'abercynonuk',
 'aberdeen',
 'aberdeencc',
 'aberdeenjobs',
 'aberdeenjos',
 'aberdeenshire',
 'aberdeenshirejobs',
 'aberlour',
 'aberlourcct',
 'abernethy',
 'aberystwyth',
 'abhari',
 'abhi',
 'abhirami',
 'abidjan',
 'abierto',
 'abilities',
 'ability',
 'abingdon',
 'abisin',
 'able',
 'aboutjob',
 'abpnews',
 'abrahammomohweoutsourceafricacom',
 'abramariita',
 'abrechnungsservice',
 'abrigo',
 'abs',
 'absa',
 'a

In [252]:
from scipy import sparse

cv_sparse = cv.fit_transform(df_bow["text"])
col = [ i for i in cv.get_feature_names()] 
temp = pd.DataFrame(cv_sparse.todense(), columns=col) 
temp

aa  aaafm  aadhar  aads  aaiwa  aaj  aajkijandhara  aajtak  \
0       0      0       0     0      0    0              0       0   
1       0      0       0     0      0    0              0       0   
2       0      0       0     0      0    0              0       0   
3       0      0       0     0      0    0              0       0   
4       0      0       0     0      0    0              0       0   
...    ..    ...     ...   ...    ...  ...            ...     ...   
22763   0      0       0     0      0    0              0       0   
22764   0      0       0     0      0    0              0       0   
22765   0      0       0     0      0    0              0       0   
22766   0      0       0     0      0    0              0       0   
22767   0      0       0     0      0    0              0       0   

       aalasijobrolengcom  aampm  ...  𝗪𝗲  𝗪𝗿𝗶𝘁𝗲  𝗮𝗻  𝗮𝗿𝗲  𝗮𝘁  𝗱𝗲𝘁𝗮𝗶𝗹𝘀  𝗳𝗼𝗿  \
0                       0      0  ...   0      0   0    0   0        0    0   
1                       0      0  ...   0      0   0    0   0        0    0   
2                       0      0  ...   0      0   0    0   0        0    0   
3                       0      0  ...   0      0   0    0   0        0    0   
4                       0      0  ...   0      0   0    0   0        0    0   
...                   ...    ...  ...  ..    ...  ..  ...  ..      ...  ...   
22763                   0      0  ...   0      0   0    0   0        0    0   
22764                   0      0  ...   0      0   0    0   0        0    0   
22765                   0      0  ...   0      0   0    0   0        0    0   
22766                   0      0  ...   0      0   0    0   0        0    0   
22767                   0      0  ...   0      0   0    0   0        0    0   

       𝗵𝗶𝗿𝗶𝗻𝗴  𝗺𝗼𝗿𝗲  𝘁𝗼  
0           0     0   0  
1           0     0   0  
2           0     0   0  
3           0     0   0  
4           0     0   0  
...       ...   ...  ..  
22763       0     0   0  
22764       0     0   0  
22765       0     0   0  
22766       0     0   0  
22767       0     0   0  

[22768 rows x 24749 columns]

In [248]:
#Transform to an array
bow.toarray()


array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]], dtype=int64)

In [241]:
print(np.matrix(bow))

[[<22768x24749 sparse matrix of type '<class 'numpy.int64'>'
	with 292000 stored elements in Compressed Sparse Row format>]]


In [242]:
bow.shape

(22768, 24749)